In [1]:
# import libraries
from sklearn import datasets
from catboost import CatBoostClassifier
from sklearn.model_selection import cross_val_score

import pandas as pd
import numpy as np

In [4]:
# load data
cancer = datasets.load_breast_cancer()
X = cancer.data
y = cancer.target

In [5]:
X.shape

(569, 30)

In [6]:
df = pd.DataFrame(X, columns=cancer.feature_names)
df.head()

mean radius  mean texture  mean perimeter  mean area  mean smoothness  \
0        17.99         10.38          122.80     1001.0          0.11840   
1        20.57         17.77          132.90     1326.0          0.08474   
2        19.69         21.25          130.00     1203.0          0.10960   
3        11.42         20.38           77.58      386.1          0.14250   
4        20.29         14.34          135.10     1297.0          0.10030   

   mean compactness  mean concavity  mean concave points  mean symmetry  \
0           0.27760          0.3001              0.14710         0.2419   
1           0.07864          0.0869              0.07017         0.1812   
2           0.15990          0.1974              0.12790         0.2069   
3           0.28390          0.2414              0.10520         0.2597   
4           0.13280          0.1980              0.10430         0.1809   

   mean fractal dimension  ...  worst radius  worst texture  worst perimeter  \
0                 0.07871  ...         25.38          17.33           184.60   
1                 0.05667  ...         24.99          23.41           158.80   
2                 0.05999  ...         23.57          25.53           152.50   
3                 0.09744  ...         14.91          26.50            98.87   
4                 0.05883  ...         22.54          16.67           152.20   

   worst area  worst smoothness  worst compactness  worst concavity  \
0      2019.0            0.1622             0.6656           0.7119   
1      1956.0            0.1238             0.1866           0.2416   
2      1709.0            0.1444             0.4245           0.4504   
3       567.7            0.2098             0.8663           0.6869   
4      1575.0            0.1374             0.2050           0.4000   

   worst concave points  worst symmetry  worst fractal dimension  
0                0.2654          0.4601                  0.11890  
1                0.1860          0.2750                  0.08902  
2                0.2430          0.3613                  0.08758  
3                0.2575          0.6638                  0.17300  
4                0.1625          0.2364                  0.07678  

[5 rows x 30 columns]

In [19]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 569 entries, 0 to 568
Data columns (total 30 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   mean radius              569 non-null    float64
 1   mean texture             569 non-null    float64
 2   mean perimeter           569 non-null    float64
 3   mean area                569 non-null    float64
 4   mean smoothness          569 non-null    float64
 5   mean compactness         569 non-null    float64
 6   mean concavity           569 non-null    float64
 7   mean concave points      569 non-null    float64
 8   mean symmetry            569 non-null    float64
 9   mean fractal dimension   569 non-null    float64
 10  radius error             569 non-null    float64
 11  texture error            569 non-null    float64
 12  perimeter error          569 non-null    float64
 13  area error               569 non-null    float64
 14  smoothness error         5

In [20]:
df.describe()

mean radius  mean texture  mean perimeter    mean area  \
count   569.000000    569.000000      569.000000   569.000000   
mean     14.127292     19.289649       91.969033   654.889104   
std       3.524049      4.301036       24.298981   351.914129   
min       6.981000      9.710000       43.790000   143.500000   
25%      11.700000     16.170000       75.170000   420.300000   
50%      13.370000     18.840000       86.240000   551.100000   
75%      15.780000     21.800000      104.100000   782.700000   
max      28.110000     39.280000      188.500000  2501.000000   

       mean smoothness  mean compactness  mean concavity  mean concave points  \
count       569.000000        569.000000      569.000000           569.000000   
mean          0.096360          0.104341        0.088799             0.048919   
std           0.014064          0.052813        0.079720             0.038803   
min           0.052630          0.019380        0.000000             0.000000   
25%           0.086370          0.064920        0.029560             0.020310   
50%           0.095870          0.092630        0.061540             0.033500   
75%           0.105300          0.130400        0.130700             0.074000   
max           0.163400          0.345400        0.426800             0.201200   

       mean symmetry  mean fractal dimension  ...  worst radius  \
count     569.000000              569.000000  ...    569.000000   
mean        0.181162                0.062798  ...     16.269190   
std         0.027414                0.007060  ...      4.833242   
min         0.106000                0.049960  ...      7.930000   
25%         0.161900                0.057700  ...     13.010000   
50%         0.179200                0.061540  ...     14.970000   
75%         0.195700                0.066120  ...     18.790000   
max         0.304000                0.097440  ...     36.040000   

       worst texture  worst perimeter   worst area  worst smoothness  \
count     569.000000       569.000000   569.000000        569.000000   
mean       25.677223       107.261213   880.583128          0.132369   
std         6.146258        33.602542   569.356993          0.022832   
min        12.020000        50.410000   185.200000          0.071170   
25%        21.080000        84.110000   515.300000          0.116600   
50%        25.410000        97.660000   686.500000          0.131300   
75%        29.720000       125.400000  1084.000000          0.146000   
max        49.540000       251.200000  4254.000000          0.222600   

       worst compactness  worst concavity  worst concave points  \
count         569.000000       569.000000            569.000000   
mean            0.254265         0.272188              0.114606   
std             0.157336         0.208624              0.065732   
min             0.027290         0.000000              0.000000   
25%             0.147200         0.114500              0.064930   
50%             0.211900         0.226700              0.099930   
75%             0.339100         0.382900              0.161400   
max             1.058000         1.252000              0.291000   

       worst symmetry  worst fractal dimension  
count      569.000000               569.000000  
mean         0.290076                 0.083946  
std          0.061867                 0.018061  
min          0.156500                 0.055040  
25%          0.250400                 0.071460  
50%          0.282200                 0.080040  
75%          0.317900                 0.092080  
max          0.663800                 0.207500  

[8 rows x 30 columns]

## Manual Tuning

In [21]:
cbc = CatBoostClassifier(max_depth=3)

In [29]:
# 5 folds cross validation, scored accuracy
cvs = cross_val_score(cbc, X, y, cv=5, scoring="roc_auc")

Learning rate set to 0.00736
0:	learn: 0.6847273	total: 2.78ms	remaining: 2.78s
1:	learn: 0.6713682	total: 7.29ms	remaining: 3.64s
2:	learn: 0.6600095	total: 9.84ms	remaining: 3.27s
3:	learn: 0.6512989	total: 12.4ms	remaining: 3.08s
4:	learn: 0.6391097	total: 15.5ms	remaining: 3.09s
5:	learn: 0.6292989	total: 17.4ms	remaining: 2.89s
6:	learn: 0.6194531	total: 19ms	remaining: 2.7s
7:	learn: 0.6106686	total: 20.3ms	remaining: 2.51s
8:	learn: 0.5988642	total: 21.4ms	remaining: 2.36s
9:	learn: 0.5890914	total: 22.6ms	remaining: 2.23s
10:	learn: 0.5797760	total: 23.7ms	remaining: 2.13s
11:	learn: 0.5698105	total: 24.9ms	remaining: 2.05s
12:	learn: 0.5613044	total: 26.3ms	remaining: 2s
13:	learn: 0.5545692	total: 27.8ms	remaining: 1.96s
14:	learn: 0.5442988	total: 29.6ms	remaining: 1.94s
15:	learn: 0.5347520	total: 31.1ms	remaining: 1.91s
16:	learn: 0.5251615	total: 32.6ms	remaining: 1.88s
17:	learn: 0.5156542	total: 34.9ms	remaining: 1.91s
18:	learn: 0.5066569	total: 37.7ms	remaining: 1.95s

273:	learn: 0.0824985	total: 364ms	remaining: 964ms
274:	learn: 0.0822901	total: 366ms	remaining: 964ms
275:	learn: 0.0821356	total: 367ms	remaining: 964ms
276:	learn: 0.0818213	total: 369ms	remaining: 963ms
277:	learn: 0.0816052	total: 371ms	remaining: 963ms
278:	learn: 0.0814385	total: 372ms	remaining: 962ms
279:	learn: 0.0812204	total: 374ms	remaining: 962ms
280:	learn: 0.0809343	total: 377ms	remaining: 964ms
281:	learn: 0.0807805	total: 378ms	remaining: 963ms
282:	learn: 0.0806126	total: 380ms	remaining: 963ms
283:	learn: 0.0803194	total: 382ms	remaining: 963ms
284:	learn: 0.0800905	total: 383ms	remaining: 961ms
285:	learn: 0.0797580	total: 386ms	remaining: 964ms
286:	learn: 0.0793923	total: 388ms	remaining: 963ms
287:	learn: 0.0792100	total: 389ms	remaining: 962ms
288:	learn: 0.0790149	total: 390ms	remaining: 960ms
289:	learn: 0.0789729	total: 392ms	remaining: 959ms
290:	learn: 0.0787829	total: 394ms	remaining: 960ms
291:	learn: 0.0786409	total: 396ms	remaining: 960ms
292:	learn: 

553:	learn: 0.0472285	total: 732ms	remaining: 589ms
554:	learn: 0.0471498	total: 734ms	remaining: 588ms
555:	learn: 0.0470384	total: 736ms	remaining: 588ms
556:	learn: 0.0469462	total: 738ms	remaining: 587ms
557:	learn: 0.0468270	total: 740ms	remaining: 586ms
558:	learn: 0.0467825	total: 741ms	remaining: 585ms
559:	learn: 0.0466960	total: 744ms	remaining: 584ms
560:	learn: 0.0466098	total: 745ms	remaining: 583ms
561:	learn: 0.0465277	total: 747ms	remaining: 582ms
562:	learn: 0.0464937	total: 749ms	remaining: 581ms
563:	learn: 0.0464638	total: 751ms	remaining: 581ms
564:	learn: 0.0464281	total: 754ms	remaining: 581ms
565:	learn: 0.0463727	total: 755ms	remaining: 579ms
566:	learn: 0.0463051	total: 756ms	remaining: 578ms
567:	learn: 0.0462401	total: 758ms	remaining: 576ms
568:	learn: 0.0461833	total: 759ms	remaining: 575ms
569:	learn: 0.0461364	total: 760ms	remaining: 574ms
570:	learn: 0.0460516	total: 761ms	remaining: 572ms
571:	learn: 0.0459654	total: 763ms	remaining: 571ms
572:	learn: 

802:	learn: 0.0325460	total: 1.09s	remaining: 269ms
803:	learn: 0.0324725	total: 1.1s	remaining: 268ms
804:	learn: 0.0324210	total: 1.1s	remaining: 267ms
805:	learn: 0.0323664	total: 1.1s	remaining: 265ms
806:	learn: 0.0323130	total: 1.1s	remaining: 264ms
807:	learn: 0.0322837	total: 1.11s	remaining: 263ms
808:	learn: 0.0322224	total: 1.11s	remaining: 262ms
809:	learn: 0.0321735	total: 1.11s	remaining: 260ms
810:	learn: 0.0321708	total: 1.11s	remaining: 260ms
811:	learn: 0.0321446	total: 1.12s	remaining: 259ms
812:	learn: 0.0321025	total: 1.12s	remaining: 258ms
813:	learn: 0.0320716	total: 1.12s	remaining: 256ms
814:	learn: 0.0320449	total: 1.12s	remaining: 255ms
815:	learn: 0.0320193	total: 1.12s	remaining: 254ms
816:	learn: 0.0320135	total: 1.13s	remaining: 252ms
817:	learn: 0.0319721	total: 1.13s	remaining: 251ms
818:	learn: 0.0319631	total: 1.13s	remaining: 250ms
819:	learn: 0.0319405	total: 1.13s	remaining: 248ms
820:	learn: 0.0319101	total: 1.13s	remaining: 247ms
821:	learn: 0.03

Learning rate set to 0.00736
0:	learn: 0.6812496	total: 2.11ms	remaining: 2.11s
1:	learn: 0.6679225	total: 4.87ms	remaining: 2.43s
2:	learn: 0.6557975	total: 6.97ms	remaining: 2.32s
3:	learn: 0.6473784	total: 8.48ms	remaining: 2.11s
4:	learn: 0.6366029	total: 9.84ms	remaining: 1.96s
5:	learn: 0.6259155	total: 11.1ms	remaining: 1.84s
6:	learn: 0.6176354	total: 12.3ms	remaining: 1.75s
7:	learn: 0.6088100	total: 14ms	remaining: 1.74s
8:	learn: 0.5985596	total: 15.3ms	remaining: 1.69s
9:	learn: 0.5889601	total: 18.4ms	remaining: 1.83s
10:	learn: 0.5803378	total: 19.7ms	remaining: 1.77s
11:	learn: 0.5713804	total: 21.3ms	remaining: 1.76s
12:	learn: 0.5623484	total: 22.9ms	remaining: 1.74s
13:	learn: 0.5516437	total: 24.2ms	remaining: 1.7s
14:	learn: 0.5426894	total: 25.4ms	remaining: 1.67s
15:	learn: 0.5364338	total: 26.6ms	remaining: 1.63s
16:	learn: 0.5261706	total: 28.1ms	remaining: 1.62s
17:	learn: 0.5170274	total: 30.2ms	remaining: 1.65s
18:	learn: 0.5098747	total: 31.4ms	remaining: 1.

...

761:	learn: 0.0374825	total: 1.02s	remaining: 319ms
762:	learn: 0.0374734	total: 1.02s	remaining: 318ms
763:	learn: 0.0374311	total: 1.03s	remaining: 317ms
764:	learn: 0.0374227	total: 1.03s	remaining: 316ms
765:	learn: 0.0373961	total: 1.03s	remaining: 315ms
766:	learn: 0.0373049	total: 1.03s	remaining: 313ms
767:	learn: 0.0372297	total: 1.03s	remaining: 312ms
768:	learn: 0.0372208	total: 1.03s	remaining: 311ms
769:	learn: 0.0371583	total: 1.04s	remaining: 310ms
770:	learn: 0.0371474	total: 1.04s	remaining: 309ms
771:	learn: 0.0370855	total: 1.04s	remaining: 307ms
772:	learn: 0.0370160	total: 1.04s	remaining: 306ms
773:	learn: 0.0369428	total: 1.04s	remaining: 305ms
774:	learn: 0.0368677	total: 1.05s	remaining: 304ms
775:	learn: 0.0368192	total: 1.05s	remaining: 302ms
776:	learn: 0.0367844	total: 1.05s	remaining: 301ms
777:	learn: 0.0367716	total: 1.05s	remaining: 300ms
778:	learn: 0.0367561	total: 1.05s	remaining: 298ms
779:	learn: 0.0367496	total: 1.05s	remaining: 297ms
780:	learn: 

24:	learn: 0.4712873	total: 31.1ms	remaining: 1.21s
25:	learn: 0.4657911	total: 33ms	remaining: 1.24s
26:	learn: 0.4603409	total: 34.9ms	remaining: 1.26s
27:	learn: 0.4543089	total: 36.6ms	remaining: 1.27s
28:	learn: 0.4470219	total: 38.6ms	remaining: 1.29s
29:	learn: 0.4410371	total: 40.3ms	remaining: 1.3s
30:	learn: 0.4352218	total: 42ms	remaining: 1.31s
31:	learn: 0.4292638	total: 43.7ms	remaining: 1.32s
32:	learn: 0.4234952	total: 45.5ms	remaining: 1.33s
33:	learn: 0.4172096	total: 47.3ms	remaining: 1.34s
34:	learn: 0.4110437	total: 49.7ms	remaining: 1.37s
35:	learn: 0.4060568	total: 53ms	remaining: 1.42s
36:	learn: 0.3999384	total: 54.3ms	remaining: 1.41s
37:	learn: 0.3931470	total: 55.6ms	remaining: 1.41s
38:	learn: 0.3878090	total: 57.5ms	remaining: 1.42s
39:	learn: 0.3835428	total: 59.7ms	remaining: 1.43s
40:	learn: 0.3797411	total: 61ms	remaining: 1.43s
41:	learn: 0.3755757	total: 62.2ms	remaining: 1.42s
42:	learn: 0.3722392	total: 63.4ms	remaining: 1.41s
43:	learn: 0.3674944	

316:	learn: 0.0869844	total: 396ms	remaining: 854ms
317:	learn: 0.0867194	total: 399ms	remaining: 856ms
318:	learn: 0.0864886	total: 401ms	remaining: 855ms
319:	learn: 0.0864018	total: 402ms	remaining: 855ms
320:	learn: 0.0861426	total: 404ms	remaining: 855ms
321:	learn: 0.0859288	total: 406ms	remaining: 855ms
322:	learn: 0.0858254	total: 408ms	remaining: 855ms
323:	learn: 0.0856690	total: 410ms	remaining: 855ms
324:	learn: 0.0854611	total: 411ms	remaining: 854ms
325:	learn: 0.0852858	total: 413ms	remaining: 854ms
326:	learn: 0.0850235	total: 415ms	remaining: 854ms
327:	learn: 0.0849757	total: 418ms	remaining: 855ms
328:	learn: 0.0849425	total: 419ms	remaining: 855ms
329:	learn: 0.0848216	total: 421ms	remaining: 856ms
330:	learn: 0.0846449	total: 423ms	remaining: 854ms
331:	learn: 0.0844188	total: 424ms	remaining: 853ms
332:	learn: 0.0843849	total: 425ms	remaining: 851ms
333:	learn: 0.0841985	total: 426ms	remaining: 850ms
334:	learn: 0.0840059	total: 428ms	remaining: 850ms
335:	learn: 

602:	learn: 0.0527827	total: 761ms	remaining: 501ms
603:	learn: 0.0527454	total: 763ms	remaining: 500ms
604:	learn: 0.0526572	total: 766ms	remaining: 500ms
605:	learn: 0.0525250	total: 767ms	remaining: 499ms
606:	learn: 0.0523801	total: 769ms	remaining: 498ms
607:	learn: 0.0523195	total: 771ms	remaining: 497ms
608:	learn: 0.0522532	total: 772ms	remaining: 496ms
609:	learn: 0.0521223	total: 774ms	remaining: 495ms
610:	learn: 0.0520188	total: 776ms	remaining: 494ms
611:	learn: 0.0519163	total: 778ms	remaining: 493ms
612:	learn: 0.0518198	total: 780ms	remaining: 492ms
613:	learn: 0.0517416	total: 782ms	remaining: 491ms
614:	learn: 0.0516642	total: 783ms	remaining: 490ms
615:	learn: 0.0515408	total: 787ms	remaining: 491ms
616:	learn: 0.0514458	total: 789ms	remaining: 489ms
617:	learn: 0.0513154	total: 790ms	remaining: 488ms
618:	learn: 0.0511581	total: 791ms	remaining: 487ms
619:	learn: 0.0510583	total: 792ms	remaining: 485ms
620:	learn: 0.0509696	total: 793ms	remaining: 484ms
621:	learn: 

890:	learn: 0.0350577	total: 1.13s	remaining: 138ms
891:	learn: 0.0350133	total: 1.13s	remaining: 137ms
892:	learn: 0.0350074	total: 1.13s	remaining: 136ms
893:	learn: 0.0349595	total: 1.13s	remaining: 135ms
894:	learn: 0.0349205	total: 1.14s	remaining: 133ms
895:	learn: 0.0349023	total: 1.14s	remaining: 132ms
896:	learn: 0.0348062	total: 1.14s	remaining: 131ms
897:	learn: 0.0347596	total: 1.14s	remaining: 130ms
898:	learn: 0.0347540	total: 1.15s	remaining: 129ms
899:	learn: 0.0347307	total: 1.15s	remaining: 127ms
900:	learn: 0.0346340	total: 1.15s	remaining: 126ms
901:	learn: 0.0345748	total: 1.15s	remaining: 125ms
902:	learn: 0.0344766	total: 1.15s	remaining: 124ms
903:	learn: 0.0343622	total: 1.15s	remaining: 123ms
904:	learn: 0.0343103	total: 1.15s	remaining: 121ms
905:	learn: 0.0342784	total: 1.16s	remaining: 120ms
906:	learn: 0.0342466	total: 1.16s	remaining: 119ms
907:	learn: 0.0342179	total: 1.16s	remaining: 118ms
908:	learn: 0.0342101	total: 1.16s	remaining: 116ms
909:	learn: 

In [30]:
# The mean value of cross validation score
print(f"The mean value of cross val score is {cvs.mean()}")

The mean value of cross val score is 0.9930813780183254


In [33]:
# Sencond Iteration with Max Depth = 5
cbc2 = CatBoostClassifier(max_depth=5)
cvs2 = cross_val_score(cbc2, X, y, cv=5, scoring="roc_auc")

Learning rate set to 0.00736
0:	learn: 0.6803684	total: 6.31ms	remaining: 6.3s
1:	learn: 0.6683804	total: 12.5ms	remaining: 6.21s
2:	learn: 0.6568557	total: 15ms	remaining: 4.97s
3:	learn: 0.6453633	total: 18.1ms	remaining: 4.51s
4:	learn: 0.6343827	total: 20.3ms	remaining: 4.04s
5:	learn: 0.6210297	total: 22.6ms	remaining: 3.74s
6:	learn: 0.6105333	total: 25.5ms	remaining: 3.61s
7:	learn: 0.6005852	total: 29.5ms	remaining: 3.65s
8:	learn: 0.5908906	total: 34.3ms	remaining: 3.78s
9:	learn: 0.5821587	total: 37.2ms	remaining: 3.68s
10:	learn: 0.5722427	total: 39.5ms	remaining: 3.55s
11:	learn: 0.5642228	total: 42ms	remaining: 3.46s
12:	learn: 0.5550924	total: 45.1ms	remaining: 3.43s
13:	learn: 0.5460142	total: 47.7ms	remaining: 3.36s
14:	learn: 0.5364855	total: 50ms	remaining: 3.28s
15:	learn: 0.5268016	total: 52.3ms	remaining: 3.21s
16:	learn: 0.5166986	total: 54.6ms	remaining: 3.16s
17:	learn: 0.5078700	total: 56.8ms	remaining: 3.1s
18:	learn: 0.5004083	total: 59.1ms	remaining: 3.05s
1

215:	learn: 0.0777633	total: 563ms	remaining: 2.04s
216:	learn: 0.0774622	total: 567ms	remaining: 2.05s
217:	learn: 0.0770047	total: 571ms	remaining: 2.05s
218:	learn: 0.0765490	total: 574ms	remaining: 2.05s
219:	learn: 0.0760974	total: 578ms	remaining: 2.05s
220:	learn: 0.0758074	total: 583ms	remaining: 2.05s
221:	learn: 0.0752909	total: 586ms	remaining: 2.05s
222:	learn: 0.0750493	total: 589ms	remaining: 2.05s
223:	learn: 0.0747275	total: 591ms	remaining: 2.05s
224:	learn: 0.0743925	total: 593ms	remaining: 2.04s
225:	learn: 0.0740195	total: 595ms	remaining: 2.04s
226:	learn: 0.0736701	total: 598ms	remaining: 2.04s
227:	learn: 0.0734163	total: 601ms	remaining: 2.03s
228:	learn: 0.0730039	total: 604ms	remaining: 2.03s
229:	learn: 0.0727199	total: 607ms	remaining: 2.03s
230:	learn: 0.0723958	total: 609ms	remaining: 2.03s
231:	learn: 0.0719774	total: 611ms	remaining: 2.02s
232:	learn: 0.0715387	total: 613ms	remaining: 2.02s
233:	learn: 0.0711785	total: 616ms	remaining: 2.02s
234:	learn: 

413:	learn: 0.0379599	total: 1.14s	remaining: 1.61s
414:	learn: 0.0378263	total: 1.14s	remaining: 1.61s
415:	learn: 0.0376974	total: 1.15s	remaining: 1.61s
416:	learn: 0.0375982	total: 1.15s	remaining: 1.61s
417:	learn: 0.0375178	total: 1.16s	remaining: 1.61s
418:	learn: 0.0373775	total: 1.16s	remaining: 1.61s
419:	learn: 0.0372758	total: 1.17s	remaining: 1.61s
420:	learn: 0.0371853	total: 1.17s	remaining: 1.61s
421:	learn: 0.0371267	total: 1.18s	remaining: 1.61s
422:	learn: 0.0370563	total: 1.18s	remaining: 1.61s
423:	learn: 0.0369024	total: 1.18s	remaining: 1.61s
424:	learn: 0.0368231	total: 1.19s	remaining: 1.6s
425:	learn: 0.0367715	total: 1.19s	remaining: 1.6s
426:	learn: 0.0366594	total: 1.19s	remaining: 1.6s
427:	learn: 0.0365664	total: 1.19s	remaining: 1.59s
428:	learn: 0.0364719	total: 1.2s	remaining: 1.59s
429:	learn: 0.0364284	total: 1.2s	remaining: 1.59s
430:	learn: 0.0363248	total: 1.2s	remaining: 1.59s
431:	learn: 0.0362600	total: 1.21s	remaining: 1.58s
432:	learn: 0.0362

603:	learn: 0.0243547	total: 1.7s	remaining: 1.11s
604:	learn: 0.0243097	total: 1.7s	remaining: 1.11s
605:	learn: 0.0242503	total: 1.71s	remaining: 1.11s
606:	learn: 0.0242150	total: 1.71s	remaining: 1.11s
607:	learn: 0.0241509	total: 1.72s	remaining: 1.11s
608:	learn: 0.0240996	total: 1.72s	remaining: 1.1s
609:	learn: 0.0240579	total: 1.72s	remaining: 1.1s
610:	learn: 0.0240172	total: 1.73s	remaining: 1.1s
611:	learn: 0.0239749	total: 1.73s	remaining: 1.1s
612:	learn: 0.0239389	total: 1.73s	remaining: 1.09s
613:	learn: 0.0238720	total: 1.74s	remaining: 1.09s
614:	learn: 0.0238161	total: 1.74s	remaining: 1.09s
615:	learn: 0.0237675	total: 1.74s	remaining: 1.08s
616:	learn: 0.0237097	total: 1.74s	remaining: 1.08s
617:	learn: 0.0236652	total: 1.75s	remaining: 1.08s
618:	learn: 0.0236260	total: 1.75s	remaining: 1.08s
619:	learn: 0.0235781	total: 1.75s	remaining: 1.07s
620:	learn: 0.0235469	total: 1.75s	remaining: 1.07s
621:	learn: 0.0235141	total: 1.76s	remaining: 1.07s
622:	learn: 0.0234

805:	learn: 0.0168359	total: 2.26s	remaining: 544ms
806:	learn: 0.0168331	total: 2.27s	remaining: 542ms
807:	learn: 0.0168234	total: 2.27s	remaining: 539ms
808:	learn: 0.0168086	total: 2.28s	remaining: 537ms
809:	learn: 0.0167814	total: 2.28s	remaining: 535ms
810:	learn: 0.0167607	total: 2.28s	remaining: 532ms
811:	learn: 0.0167127	total: 2.28s	remaining: 529ms
812:	learn: 0.0167104	total: 2.29s	remaining: 526ms
813:	learn: 0.0166732	total: 2.29s	remaining: 523ms
814:	learn: 0.0166612	total: 2.29s	remaining: 520ms
815:	learn: 0.0166208	total: 2.29s	remaining: 518ms
816:	learn: 0.0166154	total: 2.3s	remaining: 515ms
817:	learn: 0.0165686	total: 2.3s	remaining: 512ms
818:	learn: 0.0165459	total: 2.3s	remaining: 509ms
819:	learn: 0.0165151	total: 2.3s	remaining: 506ms
820:	learn: 0.0164732	total: 2.31s	remaining: 503ms
821:	learn: 0.0164466	total: 2.31s	remaining: 500ms
822:	learn: 0.0164153	total: 2.31s	remaining: 497ms
823:	learn: 0.0164089	total: 2.31s	remaining: 494ms
824:	learn: 0.01

...

75:	learn: 0.2370937	total: 192ms	remaining: 2.33s
76:	learn: 0.2342082	total: 196ms	remaining: 2.35s
77:	learn: 0.2310844	total: 200ms	remaining: 2.36s
78:	learn: 0.2292307	total: 204ms	remaining: 2.37s
79:	learn: 0.2266596	total: 209ms	remaining: 2.4s
80:	learn: 0.2241596	total: 214ms	remaining: 2.42s
81:	learn: 0.2218044	total: 216ms	remaining: 2.42s
82:	learn: 0.2194888	total: 218ms	remaining: 2.41s
83:	learn: 0.2167162	total: 221ms	remaining: 2.41s
84:	learn: 0.2140800	total: 224ms	remaining: 2.41s
85:	learn: 0.2122320	total: 227ms	remaining: 2.41s
86:	learn: 0.2098385	total: 229ms	remaining: 2.4s
87:	learn: 0.2073663	total: 231ms	remaining: 2.4s
88:	learn: 0.2055633	total: 234ms	remaining: 2.39s
89:	learn: 0.2039865	total: 236ms	remaining: 2.39s
90:	learn: 0.2016671	total: 239ms	remaining: 2.39s
91:	learn: 0.1999785	total: 241ms	remaining: 2.38s
92:	learn: 0.1974486	total: 244ms	remaining: 2.38s
93:	learn: 0.1953732	total: 246ms	remaining: 2.37s
94:	learn: 0.1936595	total: 248ms	

310:	learn: 0.0575144	total: 753ms	remaining: 1.67s
311:	learn: 0.0573942	total: 761ms	remaining: 1.68s
312:	learn: 0.0571835	total: 767ms	remaining: 1.68s
313:	learn: 0.0569838	total: 774ms	remaining: 1.69s
314:	learn: 0.0568187	total: 776ms	remaining: 1.69s
315:	learn: 0.0565119	total: 779ms	remaining: 1.69s
316:	learn: 0.0563745	total: 783ms	remaining: 1.69s
317:	learn: 0.0561999	total: 787ms	remaining: 1.69s
318:	learn: 0.0560228	total: 791ms	remaining: 1.69s
319:	learn: 0.0557878	total: 794ms	remaining: 1.69s
320:	learn: 0.0554930	total: 798ms	remaining: 1.69s
321:	learn: 0.0552739	total: 801ms	remaining: 1.69s
322:	learn: 0.0551280	total: 803ms	remaining: 1.68s
323:	learn: 0.0548779	total: 806ms	remaining: 1.68s
324:	learn: 0.0546611	total: 808ms	remaining: 1.68s
325:	learn: 0.0545470	total: 811ms	remaining: 1.68s
326:	learn: 0.0542900	total: 813ms	remaining: 1.67s
327:	learn: 0.0540874	total: 815ms	remaining: 1.67s
328:	learn: 0.0539153	total: 817ms	remaining: 1.67s
329:	learn: 

526:	learn: 0.0309740	total: 1.29s	remaining: 1.16s
527:	learn: 0.0308922	total: 1.29s	remaining: 1.15s
528:	learn: 0.0307584	total: 1.29s	remaining: 1.15s
529:	learn: 0.0306727	total: 1.3s	remaining: 1.15s
530:	learn: 0.0306065	total: 1.3s	remaining: 1.15s
531:	learn: 0.0305172	total: 1.31s	remaining: 1.15s
532:	learn: 0.0304263	total: 1.31s	remaining: 1.15s
533:	learn: 0.0303136	total: 1.31s	remaining: 1.15s
534:	learn: 0.0302218	total: 1.31s	remaining: 1.14s
535:	learn: 0.0301802	total: 1.32s	remaining: 1.14s
536:	learn: 0.0300808	total: 1.32s	remaining: 1.14s
537:	learn: 0.0299947	total: 1.32s	remaining: 1.14s
538:	learn: 0.0299258	total: 1.32s	remaining: 1.13s
539:	learn: 0.0298819	total: 1.33s	remaining: 1.13s
540:	learn: 0.0297587	total: 1.33s	remaining: 1.13s
541:	learn: 0.0296976	total: 1.33s	remaining: 1.13s
542:	learn: 0.0296438	total: 1.33s	remaining: 1.12s
543:	learn: 0.0295684	total: 1.34s	remaining: 1.12s
544:	learn: 0.0295513	total: 1.34s	remaining: 1.12s
545:	learn: 0.

762:	learn: 0.0191331	total: 1.86s	remaining: 577ms
763:	learn: 0.0191113	total: 1.86s	remaining: 574ms
764:	learn: 0.0190564	total: 1.86s	remaining: 572ms
765:	learn: 0.0190146	total: 1.87s	remaining: 570ms
766:	learn: 0.0189648	total: 1.87s	remaining: 568ms
767:	learn: 0.0189302	total: 1.87s	remaining: 566ms
768:	learn: 0.0189022	total: 1.88s	remaining: 564ms
769:	learn: 0.0188627	total: 1.88s	remaining: 561ms
770:	learn: 0.0188572	total: 1.88s	remaining: 559ms
771:	learn: 0.0188235	total: 1.88s	remaining: 556ms
772:	learn: 0.0188017	total: 1.89s	remaining: 554ms
773:	learn: 0.0187640	total: 1.89s	remaining: 551ms
774:	learn: 0.0187497	total: 1.89s	remaining: 549ms
775:	learn: 0.0187444	total: 1.89s	remaining: 547ms
776:	learn: 0.0187111	total: 1.9s	remaining: 544ms
777:	learn: 0.0186910	total: 1.9s	remaining: 542ms
778:	learn: 0.0186591	total: 1.9s	remaining: 540ms
779:	learn: 0.0186378	total: 1.9s	remaining: 537ms
780:	learn: 0.0186096	total: 1.91s	remaining: 535ms
781:	learn: 0.01

986:	learn: 0.0142242	total: 2.43s	remaining: 32ms
987:	learn: 0.0141898	total: 2.44s	remaining: 29.6ms
988:	learn: 0.0141805	total: 2.44s	remaining: 27.1ms
989:	learn: 0.0141485	total: 2.44s	remaining: 24.7ms
990:	learn: 0.0141369	total: 2.45s	remaining: 22.2ms
991:	learn: 0.0141052	total: 2.45s	remaining: 19.8ms
992:	learn: 0.0141029	total: 2.45s	remaining: 17.3ms
993:	learn: 0.0140833	total: 2.46s	remaining: 14.8ms
994:	learn: 0.0140815	total: 2.46s	remaining: 12.4ms
995:	learn: 0.0140613	total: 2.46s	remaining: 9.88ms
996:	learn: 0.0140593	total: 2.46s	remaining: 7.41ms
997:	learn: 0.0140548	total: 2.46s	remaining: 4.94ms
998:	learn: 0.0140259	total: 2.47s	remaining: 2.47ms
999:	learn: 0.0140214	total: 2.47s	remaining: 0us


In [34]:
print(f"The mean value of cross val score 2 is {cvs2.mean()}")

The mean value of cross val score 2 is 0.9933487444910634


## Grid Search

This is an automated method of hyperparameter tuning. This method works by exhaustively searching through all the values in the hyperpatameter space.

In [38]:
from sklearn.model_selection import GridSearchCV

In [51]:
grid = {
    'max_depth' : [3, 4, 5, 6],
    'n_estimators': [100, 200, 300, 400]
}

In [52]:
gscv = GridSearchCV(estimator=CatBoostClassifier(), param_grid=grid, scoring="accuracy", cv=5)

# fit the model
gscv.fit(X,y)

Learning rate set to 0.0608
0:	learn: 0.6267466	total: 2.26ms	remaining: 223ms
1:	learn: 0.5341466	total: 5.33ms	remaining: 261ms
2:	learn: 0.4681450	total: 6.62ms	remaining: 214ms
3:	learn: 0.4264899	total: 9.06ms	remaining: 218ms
4:	learn: 0.3737244	total: 12.5ms	remaining: 238ms
5:	learn: 0.3384352	total: 16ms	remaining: 251ms
6:	learn: 0.3088477	total: 18.3ms	remaining: 243ms
7:	learn: 0.2758414	total: 19.5ms	remaining: 225ms
8:	learn: 0.2478476	total: 20.7ms	remaining: 210ms
9:	learn: 0.2221684	total: 22.8ms	remaining: 205ms
10:	learn: 0.2077657	total: 24.1ms	remaining: 195ms
11:	learn: 0.1897478	total: 25.2ms	remaining: 185ms
12:	learn: 0.1785500	total: 26.4ms	remaining: 176ms
13:	learn: 0.1661830	total: 27.5ms	remaining: 169ms
14:	learn: 0.1551708	total: 28.9ms	remaining: 163ms
15:	learn: 0.1442071	total: 30.4ms	remaining: 160ms
16:	learn: 0.1374283	total: 32ms	remaining: 156ms
17:	learn: 0.1299298	total: 35.4ms	remaining: 161ms
18:	learn: 0.1252825	total: 37.7ms	remaining: 161m

8:	learn: 0.2772233	total: 22.3ms	remaining: 226ms
9:	learn: 0.2443910	total: 30.6ms	remaining: 276ms
10:	learn: 0.2270992	total: 32.6ms	remaining: 263ms
11:	learn: 0.2117790	total: 34.3ms	remaining: 251ms
12:	learn: 0.2018544	total: 36.1ms	remaining: 241ms
13:	learn: 0.1878764	total: 38ms	remaining: 234ms
14:	learn: 0.1751777	total: 44ms	remaining: 250ms
15:	learn: 0.1655262	total: 46ms	remaining: 242ms
16:	learn: 0.1589616	total: 47.5ms	remaining: 232ms
17:	learn: 0.1513318	total: 49.2ms	remaining: 224ms
18:	learn: 0.1456405	total: 50.7ms	remaining: 216ms
19:	learn: 0.1401313	total: 53ms	remaining: 212ms
20:	learn: 0.1335965	total: 54.6ms	remaining: 206ms
21:	learn: 0.1274056	total: 56.2ms	remaining: 199ms
22:	learn: 0.1246809	total: 57.4ms	remaining: 192ms
23:	learn: 0.1208732	total: 58.5ms	remaining: 185ms
24:	learn: 0.1184301	total: 59.6ms	remaining: 179ms
25:	learn: 0.1157692	total: 60.8ms	remaining: 173ms
26:	learn: 0.1116120	total: 62.3ms	remaining: 169ms
27:	learn: 0.1100929	t

20:	learn: 0.1325172	total: 37.1ms	remaining: 140ms
21:	learn: 0.1276547	total: 39.7ms	remaining: 141ms
22:	learn: 0.1245347	total: 42.8ms	remaining: 143ms
23:	learn: 0.1217287	total: 44.6ms	remaining: 141ms
24:	learn: 0.1163834	total: 46.9ms	remaining: 141ms
25:	learn: 0.1129572	total: 48.9ms	remaining: 139ms
26:	learn: 0.1092651	total: 50.7ms	remaining: 137ms
27:	learn: 0.1074005	total: 52.4ms	remaining: 135ms
28:	learn: 0.1042097	total: 55.1ms	remaining: 135ms
29:	learn: 0.1010695	total: 59.7ms	remaining: 139ms
30:	learn: 0.0988230	total: 61.7ms	remaining: 137ms
31:	learn: 0.0963427	total: 64.9ms	remaining: 138ms
32:	learn: 0.0927198	total: 68.8ms	remaining: 140ms
33:	learn: 0.0909286	total: 70.1ms	remaining: 136ms
34:	learn: 0.0898179	total: 71.2ms	remaining: 132ms
35:	learn: 0.0886953	total: 72.4ms	remaining: 129ms
36:	learn: 0.0872055	total: 73.6ms	remaining: 125ms
37:	learn: 0.0843905	total: 75.1ms	remaining: 122ms
38:	learn: 0.0833207	total: 77.6ms	remaining: 121ms
39:	learn: 0

152:	learn: 0.0399314	total: 213ms	remaining: 65.6ms
153:	learn: 0.0397970	total: 215ms	remaining: 64.3ms
154:	learn: 0.0395295	total: 218ms	remaining: 63.4ms
155:	learn: 0.0391317	total: 220ms	remaining: 62.1ms
156:	learn: 0.0389783	total: 222ms	remaining: 60.8ms
157:	learn: 0.0386285	total: 224ms	remaining: 59.5ms
158:	learn: 0.0382288	total: 225ms	remaining: 58.1ms
159:	learn: 0.0380112	total: 228ms	remaining: 56.9ms
160:	learn: 0.0378145	total: 229ms	remaining: 55.6ms
161:	learn: 0.0375576	total: 231ms	remaining: 54.3ms
162:	learn: 0.0373617	total: 233ms	remaining: 53ms
163:	learn: 0.0369156	total: 235ms	remaining: 51.7ms
164:	learn: 0.0367323	total: 237ms	remaining: 50.3ms
165:	learn: 0.0365462	total: 238ms	remaining: 48.8ms
166:	learn: 0.0363765	total: 239ms	remaining: 47.3ms
167:	learn: 0.0361962	total: 241ms	remaining: 45.8ms
168:	learn: 0.0359337	total: 242ms	remaining: 44.3ms
169:	learn: 0.0356460	total: 243ms	remaining: 42.9ms
170:	learn: 0.0354708	total: 244ms	remaining: 41

193:	learn: 0.0310220	total: 272ms	remaining: 8.4ms
194:	learn: 0.0309295	total: 274ms	remaining: 7.02ms
195:	learn: 0.0308262	total: 277ms	remaining: 5.65ms
196:	learn: 0.0305779	total: 279ms	remaining: 4.24ms
197:	learn: 0.0304049	total: 281ms	remaining: 2.84ms
198:	learn: 0.0303058	total: 283ms	remaining: 1.42ms
199:	learn: 0.0301750	total: 285ms	remaining: 0us
Learning rate set to 0.0322
0:	learn: 0.6573136	total: 2.2ms	remaining: 437ms
1:	learn: 0.6064773	total: 3.78ms	remaining: 374ms
2:	learn: 0.5646116	total: 5.03ms	remaining: 330ms
3:	learn: 0.5351507	total: 6.23ms	remaining: 305ms
4:	learn: 0.5062713	total: 7.43ms	remaining: 290ms
5:	learn: 0.4760955	total: 10.1ms	remaining: 327ms
6:	learn: 0.4525204	total: 11.5ms	remaining: 317ms
7:	learn: 0.4226819	total: 12.7ms	remaining: 304ms
8:	learn: 0.3966584	total: 13.8ms	remaining: 294ms
9:	learn: 0.3694244	total: 15.2ms	remaining: 289ms
10:	learn: 0.3519943	total: 17.2ms	remaining: 295ms
11:	learn: 0.3342643	total: 18.6ms	remaining

...

136:	learn: 0.0488101	total: 610ms	remaining: 1.17s
137:	learn: 0.0483117	total: 617ms	remaining: 1.17s
138:	learn: 0.0480360	total: 625ms	remaining: 1.17s
139:	learn: 0.0476992	total: 632ms	remaining: 1.17s
140:	learn: 0.0471756	total: 638ms	remaining: 1.17s
141:	learn: 0.0468789	total: 643ms	remaining: 1.17s
142:	learn: 0.0463717	total: 647ms	remaining: 1.16s
143:	learn: 0.0460079	total: 651ms	remaining: 1.16s
144:	learn: 0.0457382	total: 657ms	remaining: 1.16s
145:	learn: 0.0453538	total: 661ms	remaining: 1.15s
146:	learn: 0.0450777	total: 665ms	remaining: 1.15s
147:	learn: 0.0446440	total: 670ms	remaining: 1.14s
148:	learn: 0.0443218	total: 674ms	remaining: 1.13s
149:	learn: 0.0439907	total: 678ms	remaining: 1.13s
150:	learn: 0.0435840	total: 682ms	remaining: 1.12s
151:	learn: 0.0433096	total: 686ms	remaining: 1.12s
152:	learn: 0.0429343	total: 690ms	remaining: 1.11s
153:	learn: 0.0425437	total: 694ms	remaining: 1.11s
154:	learn: 0.0421793	total: 699ms	remaining: 1.1s
155:	learn: 0

305:	learn: 0.0166144	total: 1.38s	remaining: 425ms
306:	learn: 0.0165854	total: 1.39s	remaining: 422ms
307:	learn: 0.0165005	total: 1.4s	remaining: 418ms
308:	learn: 0.0163993	total: 1.41s	remaining: 415ms
309:	learn: 0.0163600	total: 1.41s	remaining: 411ms
310:	learn: 0.0162875	total: 1.42s	remaining: 406ms
311:	learn: 0.0162377	total: 1.42s	remaining: 402ms
312:	learn: 0.0161776	total: 1.43s	remaining: 397ms
313:	learn: 0.0161361	total: 1.43s	remaining: 392ms
314:	learn: 0.0160505	total: 1.44s	remaining: 388ms
315:	learn: 0.0160011	total: 1.44s	remaining: 383ms
316:	learn: 0.0159167	total: 1.45s	remaining: 378ms
317:	learn: 0.0158258	total: 1.45s	remaining: 374ms
318:	learn: 0.0157492	total: 1.45s	remaining: 369ms
319:	learn: 0.0156687	total: 1.46s	remaining: 365ms
320:	learn: 0.0155791	total: 1.46s	remaining: 360ms
321:	learn: 0.0155067	total: 1.47s	remaining: 355ms
322:	learn: 0.0153868	total: 1.47s	remaining: 351ms
323:	learn: 0.0153195	total: 1.48s	remaining: 346ms
324:	learn: 0

131:	learn: 0.0474493	total: 283ms	remaining: 360ms
132:	learn: 0.0472871	total: 287ms	remaining: 360ms
133:	learn: 0.0470417	total: 290ms	remaining: 359ms
134:	learn: 0.0467953	total: 293ms	remaining: 358ms
135:	learn: 0.0463890	total: 297ms	remaining: 358ms
136:	learn: 0.0459854	total: 300ms	remaining: 357ms
137:	learn: 0.0457114	total: 303ms	remaining: 356ms
138:	learn: 0.0453807	total: 307ms	remaining: 355ms
139:	learn: 0.0451252	total: 310ms	remaining: 354ms
140:	learn: 0.0450945	total: 314ms	remaining: 354ms
141:	learn: 0.0446942	total: 317ms	remaining: 352ms
142:	learn: 0.0444827	total: 319ms	remaining: 350ms
143:	learn: 0.0441847	total: 321ms	remaining: 347ms
144:	learn: 0.0437932	total: 323ms	remaining: 345ms
145:	learn: 0.0436264	total: 324ms	remaining: 342ms
146:	learn: 0.0435097	total: 326ms	remaining: 340ms
147:	learn: 0.0433608	total: 329ms	remaining: 338ms
148:	learn: 0.0431585	total: 332ms	remaining: 336ms
149:	learn: 0.0428618	total: 334ms	remaining: 334ms
150:	learn: 

299:	learn: 0.0205667	total: 652ms	remaining: 0us


GridSearchCV(cv=5,
             estimator=<catboost.core.CatBoostClassifier object at 0x122727f10>,
             param_grid={'max_depth': [3, 4, 5, 6],
                         'n_estimators': [100, 200, 300, 400]},
             scoring='accuracy')

In [54]:
# Print besties
print(f"best estimator \t: {gscv.best_estimator_}")
print(f"best score \t: {gscv.best_score_}")
print(f"best params \t: {gscv.best_params_}")
print(f"best index \t: {gscv.best_index_}")

best estimator 	: <catboost.core.CatBoostClassifier object at 0x12187a690>
best score 	: 0.9789473684210528
best params 	: {'max_depth': 4, 'n_estimators': 300}
best index 	: 6


In [56]:
# Print Input values
print(f"estimator \t: {gscv.estimator}")
print(f"param grid \t: {gscv.param_grid}")
print(f"scoring \t: {gscv.scoring}")

estimator 	: <catboost.core.CatBoostClassifier object at 0x122727f10>
param grid 	: {'max_depth': [3, 4, 5, 6], 'n_estimators': [100, 200, 300, 400]}
scoring 	: accuracy


## Random Search
As the name implies, this method searches the hyperparameters space randomly for the best performance. This makes it fast and less computation intensive. 

The hyperparameters were given as a statistical distribution instead of set of values.

In [73]:
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint

In [75]:
param_dist = {
    "learning_rate": np.linspace(0,0.2,5),
    "max_depth": randint(3, 10)
}

In [76]:
param_dist

{'learning_rate': array([0.   , 0.025, 0.05 , 0.075, 0.1  ]),
 'max_depth': <scipy.stats._distn_infrastructure.rv_frozen at 0x123df13d0>}

In [77]:
rscv = RandomizedSearchCV(estimator=CatBoostClassifier(), param_distributions=param_dist, scoring="accuracy", cv=5)

# Fit the model
rscv.fit(X,y)

0:	learn: 0.6172882	total: 21.7ms	remaining: 21.7s
1:	learn: 0.5492672	total: 33.6ms	remaining: 16.8s
2:	learn: 0.4920116	total: 45.1ms	remaining: 15s
3:	learn: 0.4430869	total: 56.7ms	remaining: 14.1s
4:	learn: 0.4038190	total: 67.5ms	remaining: 13.4s
5:	learn: 0.3644715	total: 77.8ms	remaining: 12.9s
6:	learn: 0.3235462	total: 88.3ms	remaining: 12.5s
7:	learn: 0.2933550	total: 98.1ms	remaining: 12.2s
8:	learn: 0.2664160	total: 109ms	remaining: 12s
9:	learn: 0.2485557	total: 121ms	remaining: 11.9s
10:	learn: 0.2297741	total: 131ms	remaining: 11.8s
11:	learn: 0.2110972	total: 141ms	remaining: 11.6s
12:	learn: 0.1973285	total: 150ms	remaining: 11.4s
13:	learn: 0.1834900	total: 159ms	remaining: 11.2s
14:	learn: 0.1718737	total: 169ms	remaining: 11.1s
15:	learn: 0.1602056	total: 178ms	remaining: 11s
16:	learn: 0.1520731	total: 188ms	remaining: 10.9s
17:	learn: 0.1431244	total: 197ms	remaining: 10.8s
18:	learn: 0.1343821	total: 207ms	remaining: 10.7s
19:	learn: 0.1279449	total: 216ms	remai

167:	learn: 0.0064783	total: 2.26s	remaining: 11.2s
168:	learn: 0.0064164	total: 2.28s	remaining: 11.2s
169:	learn: 0.0063674	total: 2.29s	remaining: 11.2s
170:	learn: 0.0063024	total: 2.3s	remaining: 11.2s
171:	learn: 0.0062427	total: 2.31s	remaining: 11.1s
172:	learn: 0.0061921	total: 2.32s	remaining: 11.1s
173:	learn: 0.0061388	total: 2.33s	remaining: 11.1s
174:	learn: 0.0060818	total: 2.34s	remaining: 11s
175:	learn: 0.0060234	total: 2.35s	remaining: 11s
176:	learn: 0.0059690	total: 2.36s	remaining: 11s
177:	learn: 0.0059131	total: 2.37s	remaining: 11s
178:	learn: 0.0058553	total: 2.38s	remaining: 10.9s
179:	learn: 0.0058020	total: 2.39s	remaining: 10.9s
180:	learn: 0.0057475	total: 2.4s	remaining: 10.9s
181:	learn: 0.0056989	total: 2.41s	remaining: 10.8s
182:	learn: 0.0056477	total: 2.42s	remaining: 10.8s
183:	learn: 0.0055986	total: 2.43s	remaining: 10.8s
184:	learn: 0.0055518	total: 2.44s	remaining: 10.7s
185:	learn: 0.0055040	total: 2.45s	remaining: 10.7s
186:	learn: 0.0054586	

329:	learn: 0.0025275	total: 4.11s	remaining: 8.34s
330:	learn: 0.0025154	total: 4.12s	remaining: 8.33s
331:	learn: 0.0025044	total: 4.14s	remaining: 8.33s
332:	learn: 0.0024956	total: 4.15s	remaining: 8.31s
333:	learn: 0.0024880	total: 4.16s	remaining: 8.3s
334:	learn: 0.0024784	total: 4.17s	remaining: 8.28s
335:	learn: 0.0024708	total: 4.18s	remaining: 8.26s
336:	learn: 0.0024585	total: 4.19s	remaining: 8.25s
337:	learn: 0.0024514	total: 4.2s	remaining: 8.23s
338:	learn: 0.0024408	total: 4.21s	remaining: 8.22s
339:	learn: 0.0024315	total: 4.22s	remaining: 8.2s
340:	learn: 0.0024238	total: 4.24s	remaining: 8.2s
341:	learn: 0.0024169	total: 4.26s	remaining: 8.19s
342:	learn: 0.0024073	total: 4.27s	remaining: 8.18s
343:	learn: 0.0023972	total: 4.28s	remaining: 8.17s
344:	learn: 0.0023902	total: 4.3s	remaining: 8.16s
345:	learn: 0.0023830	total: 4.31s	remaining: 8.15s
346:	learn: 0.0023751	total: 4.32s	remaining: 8.13s
347:	learn: 0.0023663	total: 4.33s	remaining: 8.12s
348:	learn: 0.002

494:	learn: 0.0015653	total: 6.36s	remaining: 6.49s
495:	learn: 0.0015640	total: 6.39s	remaining: 6.49s
496:	learn: 0.0015614	total: 6.4s	remaining: 6.47s
497:	learn: 0.0015585	total: 6.41s	remaining: 6.47s
498:	learn: 0.0015550	total: 6.43s	remaining: 6.45s
499:	learn: 0.0015507	total: 6.44s	remaining: 6.44s
500:	learn: 0.0015482	total: 6.45s	remaining: 6.43s
501:	learn: 0.0015477	total: 6.47s	remaining: 6.41s
502:	learn: 0.0015443	total: 6.48s	remaining: 6.4s
503:	learn: 0.0015415	total: 6.49s	remaining: 6.38s
504:	learn: 0.0015379	total: 6.5s	remaining: 6.37s
505:	learn: 0.0015361	total: 6.51s	remaining: 6.36s
506:	learn: 0.0015319	total: 6.53s	remaining: 6.34s
507:	learn: 0.0015319	total: 6.54s	remaining: 6.33s
508:	learn: 0.0015295	total: 6.55s	remaining: 6.32s
509:	learn: 0.0015270	total: 6.58s	remaining: 6.32s
510:	learn: 0.0015260	total: 6.59s	remaining: 6.31s
511:	learn: 0.0015219	total: 6.61s	remaining: 6.3s
512:	learn: 0.0015184	total: 6.62s	remaining: 6.29s
513:	learn: 0.00

662:	learn: 0.0013187	total: 8.61s	remaining: 4.37s
663:	learn: 0.0013186	total: 8.63s	remaining: 4.37s
664:	learn: 0.0013172	total: 8.64s	remaining: 4.35s
665:	learn: 0.0013135	total: 8.66s	remaining: 4.34s
666:	learn: 0.0013113	total: 8.67s	remaining: 4.33s
667:	learn: 0.0013113	total: 8.68s	remaining: 4.31s
668:	learn: 0.0013092	total: 8.69s	remaining: 4.3s
669:	learn: 0.0013071	total: 8.7s	remaining: 4.29s
670:	learn: 0.0013071	total: 8.71s	remaining: 4.27s
671:	learn: 0.0013070	total: 8.73s	remaining: 4.26s
672:	learn: 0.0013064	total: 8.74s	remaining: 4.25s
673:	learn: 0.0013064	total: 8.75s	remaining: 4.23s
674:	learn: 0.0013064	total: 8.76s	remaining: 4.22s
675:	learn: 0.0013063	total: 8.78s	remaining: 4.21s
676:	learn: 0.0013033	total: 8.79s	remaining: 4.19s
677:	learn: 0.0013033	total: 8.8s	remaining: 4.18s
678:	learn: 0.0013033	total: 8.81s	remaining: 4.17s
679:	learn: 0.0013032	total: 8.83s	remaining: 4.15s
680:	learn: 0.0013016	total: 8.84s	remaining: 4.14s
681:	learn: 0.0

...

375:	learn: 0.0080281	total: 1.95s	remaining: 3.24s
376:	learn: 0.0080209	total: 1.96s	remaining: 3.24s
377:	learn: 0.0079839	total: 1.97s	remaining: 3.24s
378:	learn: 0.0079151	total: 1.98s	remaining: 3.24s
379:	learn: 0.0079112	total: 1.98s	remaining: 3.24s
380:	learn: 0.0078618	total: 1.99s	remaining: 3.24s
381:	learn: 0.0078233	total: 2s	remaining: 3.23s
382:	learn: 0.0078064	total: 2s	remaining: 3.22s
383:	learn: 0.0078004	total: 2.01s	remaining: 3.22s
384:	learn: 0.0077990	total: 2.01s	remaining: 3.21s
385:	learn: 0.0077970	total: 2.02s	remaining: 3.21s
386:	learn: 0.0077936	total: 2.02s	remaining: 3.2s
387:	learn: 0.0077602	total: 2.02s	remaining: 3.19s
388:	learn: 0.0077601	total: 2.03s	remaining: 3.19s
389:	learn: 0.0076951	total: 2.03s	remaining: 3.18s
390:	learn: 0.0076466	total: 2.04s	remaining: 3.17s
391:	learn: 0.0075898	total: 2.04s	remaining: 3.17s
392:	learn: 0.0075855	total: 2.05s	remaining: 3.16s
393:	learn: 0.0075261	total: 2.05s	remaining: 3.15s
394:	learn: 0.00750

561:	learn: 0.0054297	total: 2.93s	remaining: 2.28s
562:	learn: 0.0054296	total: 2.94s	remaining: 2.28s
563:	learn: 0.0054296	total: 2.94s	remaining: 2.28s
564:	learn: 0.0054296	total: 2.95s	remaining: 2.27s
565:	learn: 0.0054296	total: 2.96s	remaining: 2.27s
566:	learn: 0.0053959	total: 2.96s	remaining: 2.26s
567:	learn: 0.0053607	total: 2.96s	remaining: 2.25s
568:	learn: 0.0053607	total: 2.97s	remaining: 2.25s
569:	learn: 0.0053417	total: 2.97s	remaining: 2.24s
570:	learn: 0.0053108	total: 2.98s	remaining: 2.23s
571:	learn: 0.0052802	total: 2.98s	remaining: 2.23s
572:	learn: 0.0052802	total: 2.98s	remaining: 2.22s
573:	learn: 0.0052786	total: 2.99s	remaining: 2.22s
574:	learn: 0.0052786	total: 2.99s	remaining: 2.21s
575:	learn: 0.0052786	total: 2.99s	remaining: 2.2s
576:	learn: 0.0052786	total: 3s	remaining: 2.2s
577:	learn: 0.0052775	total: 3s	remaining: 2.19s
578:	learn: 0.0052775	total: 3s	remaining: 2.19s
579:	learn: 0.0052775	total: 3.01s	remaining: 2.18s
580:	learn: 0.0052775	t

757:	learn: 0.0042668	total: 3.9s	remaining: 1.24s
758:	learn: 0.0042471	total: 3.9s	remaining: 1.24s
759:	learn: 0.0042471	total: 3.91s	remaining: 1.23s
760:	learn: 0.0042471	total: 3.92s	remaining: 1.23s
761:	learn: 0.0042471	total: 3.92s	remaining: 1.23s
762:	learn: 0.0042471	total: 3.93s	remaining: 1.22s
763:	learn: 0.0042460	total: 3.93s	remaining: 1.21s
764:	learn: 0.0042460	total: 3.93s	remaining: 1.21s
765:	learn: 0.0042295	total: 3.94s	remaining: 1.2s
766:	learn: 0.0042294	total: 3.94s	remaining: 1.2s
767:	learn: 0.0042294	total: 3.95s	remaining: 1.19s
768:	learn: 0.0042294	total: 3.95s	remaining: 1.19s
769:	learn: 0.0042294	total: 3.95s	remaining: 1.18s
770:	learn: 0.0042180	total: 3.96s	remaining: 1.18s
771:	learn: 0.0041993	total: 3.96s	remaining: 1.17s
772:	learn: 0.0041922	total: 3.96s	remaining: 1.16s
773:	learn: 0.0041868	total: 3.97s	remaining: 1.16s
774:	learn: 0.0041673	total: 3.97s	remaining: 1.15s
775:	learn: 0.0041546	total: 3.97s	remaining: 1.15s
776:	learn: 0.00

939:	learn: 0.0037675	total: 4.67s	remaining: 298ms
940:	learn: 0.0037507	total: 4.68s	remaining: 293ms
941:	learn: 0.0037403	total: 4.68s	remaining: 288ms
942:	learn: 0.0037394	total: 4.69s	remaining: 284ms
943:	learn: 0.0037394	total: 4.71s	remaining: 279ms
944:	learn: 0.0037394	total: 4.71s	remaining: 274ms
945:	learn: 0.0037394	total: 4.71s	remaining: 269ms
946:	learn: 0.0037394	total: 4.72s	remaining: 264ms
947:	learn: 0.0037394	total: 4.72s	remaining: 259ms
948:	learn: 0.0037394	total: 4.73s	remaining: 254ms
949:	learn: 0.0037394	total: 4.73s	remaining: 249ms
950:	learn: 0.0037394	total: 4.74s	remaining: 244ms
951:	learn: 0.0037394	total: 4.74s	remaining: 239ms
952:	learn: 0.0037394	total: 4.75s	remaining: 234ms
953:	learn: 0.0037394	total: 4.75s	remaining: 229ms
954:	learn: 0.0037394	total: 4.75s	remaining: 224ms
955:	learn: 0.0037394	total: 4.76s	remaining: 219ms
956:	learn: 0.0037393	total: 4.76s	remaining: 214ms
957:	learn: 0.0037393	total: 4.77s	remaining: 209ms
958:	learn: 

RandomizedSearchCV(cv=5,
                   estimator=<catboost.core.CatBoostClassifier object at 0x123456510>,
                   param_distributions={'learning_rate': array([0.   , 0.025, 0.05 , 0.075, 0.1  ]),
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x123df13d0>},
                   scoring='accuracy')

In [78]:
# Print besties
print(f"best estimator \t: {rscv.best_estimator_}")
print(f"best score \t: {rscv.best_score_}")
print(f"best params \t: {rscv.best_params_}")
print(f"best index \t: {rscv.best_index_}")

best estimator 	: <catboost.core.CatBoostClassifier object at 0x121906b50>
best score 	: 0.9736221083682658
best params 	: {'learning_rate': 0.025, 'max_depth': 6}
best index 	: 5
